# Source of Code:
This code reproduces the results of the “Statistical supervised meta-ensemble algorithm for medical record linkage” paper. The vast majority of this code was sourced from the original paper’s GitHub repository. The original code has been slightly modified and amended.

K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.

# 1. Producing the FEBRL Dataset

In [1]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
import recordlinkage as rl, pandas as pd, numpy as np
from recordlinkage.datasets import load_febrl4, load_febrl1, load_febrl2, load_febrl3
from IPython.display import clear_output

## 1.1 Producing febrl3_UNSW.csv

In [2]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df, true_links_ab = load_febrl3(return_links=True)

In [3]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df['date_of_birth']  = pd.to_datetime(df['date_of_birth'], errors = 'coerce')
df['day'] = df['date_of_birth'].dt.strftime('%d')
df['month'] = df['date_of_birth'].dt.strftime('%m')
df['year'] = df['date_of_birth'].dt.strftime('%Y')

df['postcode'] =   df['postcode'].fillna('0000')
df['postcode'] = df['postcode'].astype(int)

df['street_number'] =   df['street_number'].fillna('0')
df['street_number'] = df['street_number'].astype(int)

df = df.drop(["soc_sec_id",  "date_of_birth"], axis=1)

for col in ["surname", "given_name", "address_1", "address_2", "day", "month"]:
    df[col] = df[col].fillna('')
    df[col] = df[col].astype(str)

all_fields = df.columns.values.tolist()

print("All fields:", all_fields)
df.head()

All fields: ['given_name', 'surname', 'street_number', 'address_1', 'address_2', 'suburb', 'postcode', 'state', 'day', 'month', 'year']
CPU times: user 39.7 ms, sys: 1.56 ms, total: 41.3 ms
Wall time: 40.8 ms


given_name   surname  street_number        address_1  \
rec_id                                                                
rec-1496-org     mitchell     green              7    wallaby place   
rec-552-dup-3      harley  mccarthy            177    pridhamstreet   
rec-988-dup-1    madeline     mason             54  hoseason street   
rec-1716-dup-1   isabelle                       23    gundulu place   
rec-1213-org       taylor  hathaway              7   yuranigh court   

                             address_2     suburb  postcode state day month  \
rec_id                                                                        
rec-1496-org                    delmar  cleveland      2119    sa  09    04   
rec-552-dup-3                   milton    marsden      3165   nsw  19    04   
rec-988-dup-1   lakefront retrmnt vlge  granville      4881   nsw  28    11   
rec-1716-dup-1               currin ga   utakarra      2193    wa  19    11   
rec-1213-org            brentwood vlge        NaN      4220   nsw  07    12   

                year  
rec_id                
rec-1496-org    1956  
rec-552-dup-3   1908  
rec-988-dup-1   1908  
rec-1716-dup-1  1992  
rec-1213-org    1999

In [4]:
%%time

'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df['match_id'] = [-1]*len(df)

for i in range(len(true_links_ab)):
    k0  = true_links_ab[i][0]
    k1  = true_links_ab[i][1]
    df.at[k0, "match_id"] = i
    df.at[k1, "match_id"] = i
    #print("Processed:", i)
    #clear_output(wait=True)

CPU times: user 83.6 ms, sys: 1.5 ms, total: 85.1 ms
Wall time: 84.4 ms


In [5]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df.to_csv("febrl3_UNSW.csv", index=True)

## 1.2 Producing febrl4_UNSW.csv

In [6]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df_a, df_b, true_links_ab = load_febrl4(return_links=True) # use this for load_febrl4
#df, true_links_ab = load_febrl3(return_links=True)
# WARNING: load_febrl2 and load_febrl3 does not suit this code, need further process

In [7]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df = df_a.append(df_b) # use for load_febrl4

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3144080809.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df_a.append(df_b) # use for load_febrl4


In [8]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df['date_of_birth']  = pd.to_datetime(df['date_of_birth'], errors = 'coerce')
df['day'] = df['date_of_birth'].dt.strftime('%d')
df['month'] = df['date_of_birth'].dt.strftime('%m')
df['year'] = df['date_of_birth'].dt.strftime('%Y')

df['postcode'] =   df['postcode'].fillna('0000')
df['postcode'] = df['postcode'].astype(int)

df['street_number'] =   df['street_number'].fillna('0')
df['street_number'] = df['street_number'].astype(int)

df = df.drop(["soc_sec_id",  "date_of_birth"], axis=1)

for col in ["surname", "given_name", "address_1", "address_2", "day", "month"]:
    df[col] = df[col].fillna('')
    df[col] = df[col].astype(str)

all_fields = df.columns.values.tolist()

print("All fields:", all_fields)
df.head()

All fields: ['given_name', 'surname', 'street_number', 'address_1', 'address_2', 'suburb', 'postcode', 'state', 'day', 'month', 'year']
CPU times: user 75.6 ms, sys: 2.19 ms, total: 77.7 ms
Wall time: 76.9 ms


given_name   surname  street_number            address_1  \
rec_id                                                                  
rec-1070-org   michaela   neumann              8       stanley street   
rec-1016-org   courtney   painter             12    pinkerton circuit   
rec-4405-org    charles     green             38  salkauskas crescent   
rec-1288-org    vanessa      parr            905       macquoid place   
rec-3585-org    mikayla  malloney             37        randwick road   

                      address_2            suburb  postcode state day month  \
rec_id                                                                        
rec-1070-org              miami     winston hills      4223   nsw  11    11   
rec-1016-org         bega flats         richlands      4560   vic  14    12   
rec-4405-org               kela             dapto      4566   nsw  30    09   
rec-1288-org  broadbridge manor     south grafton      2135    sa  19    11   
rec-3585-org            avalind  hoppers crossing      4552   vic  08    02   

              year  
rec_id              
rec-1070-org  1915  
rec-1016-org  1916  
rec-4405-org  1948  
rec-1288-org  1995  
rec-3585-org  1986

In [9]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df['match_id'] = [-1]*len(df)

for i in range(len(true_links_ab)):
    k0  = true_links_ab[i][0]
    k1  = true_links_ab[i][1]
    df.at[k0, "match_id"] = i
    df.at[k1, "match_id"] = i
    #print("Processed:", i)
    #clear_output(wait=True)

CPU times: user 65.5 ms, sys: 1.32 ms, total: 66.8 ms
Wall time: 66.5 ms


In [10]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df.to_csv("febrl4_UNSW.csv", index=True)

# 2. Producing the ePBRN Dataset

## 2.1 Producing ePBRN_D_dup.csv

In [11]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
from numpy.random import choice
import random
import sys

In [12]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
inputfile = 'ePBRN_D_original' 
outputfile = 'ePBRN_D_dup'

In [13]:
'''
This code was slightly modified from the original source code provided by the paper’s authors

Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Input the percentage of  [2, 3, 4] shared records in one linkage:
count_shared = [1.68+21.0659, 1.9986 + 0.0471, 0.05]

# Assigning the weights for each type of error:

abr = 1 # abbreviation on surname: Michael -> M
jwd1 = 1 # join with dash: John Peter -> John-Peter, join surname and given name into surname
jwd2 = 1 # join with dash: John Peter -> John-Peter, join surname and given name into given name
jwb1 = 1 # join with blank: 
jwb2 = 1 # join with blank: 
drf = 1 # drop all tokens in any field
dlc1 = 1 # drop last character in surname: Peter -> Pete
dlc2 = 1 # drop last character in given name
swn = 1 # swap surname and given name: John Peter -> Peter John
#swc1 = 1 # swap character in surname: Peter -> Petre
#swc2 = 1 # swap character in given name: Peter -> Petre
swd = 1 # swap day and month fields: 12/04 -> 04/12
rsd = 1 # reset day and month: 12/04/1991 -> 01/01/1991
chy = 1 # change year of birth by a margin of (+/-)5 
#drz1 = 1 # drop leading zeros from day of birth: 02/04 -> 2/04
#drz2 = 1 # drop leading zeros from month of birth: 02/04 -> 02/4
chz = 1 # change any number of digit from zip code
mar = 1 # change the whole token of surname: Mary Ward -> Mary Winston
twi = 1 # duplicate all fields except given name: Micheal Williams -> Leo Williams
add = 1 # change the whole 3 fields of address by randomly replacing each field by any other row

all_error_types = ['abr','jwd1','jwd2','jwb1','jwb2' ,'drf','dlc1','dlc2','swn',
                   'rsd','chy','chz','mar','twi','add']
all_error_weights = [abr, jwd1, jwd2, jwb1, jwb2, drf, dlc1, dlc2, swn, rsd, chy, chz, mar, twi, add]
all_error_weights = all_error_weights/sum(np.asarray(all_error_weights))

def process_record(rc):
    no_error = np.random.poisson(1, 1)
    errortypes = choice(all_error_types, no_error, p=all_error_weights)
    for errortype in errortypes:
        if errortype == 'abr':
            if len(rc["surname"])>0:
                #rc["surname"] = rc["surname"][0]
                rc.at["surname"] = rc["surname"][0]
        if errortype == 'jwd1':
            rc.at["surname"] = rc["surname"]+'-' +rc["given_name"]
            rc.at["given_name"] = ''
        if errortype == 'jwd2':
            rc.at["given_name"] = rc["surname"]+'-' +rc["given_name"]
            rc.at["surname"] = ''
        if errortype == 'jwb1':
            rc.at["surname"] = rc["surname"]+' ' +rc["given_name"]
            rc.at["given_name"] = ''
        if errortype == 'jwb2':
            rc.at["given_name"] = rc["surname"]+' ' +rc["given_name"]
            rc.at["surname"] = ''
        if errortype == 'drf':    
            selected_field = random.choice(all_fields)
            rc.at[selected_field] = ''
        if errortype == 'dlc1':
            if len(rc["surname"])>0:
                rc.at["surname"] = rc['surname'][0:-1]
        if errortype == 'dlc2':
            if len(rc["given_name"])>0:
                rc.at["given_name"] = rc['given_name'][0:-1]
        if errortype == 'swn':
            temp = rc['given_name']
            rc.at["given_name"] = rc['surname']
            rc.at["surname"] = temp
        if errortype == 'swd': 
            temp = rc['day']
            rc.at['day'] = rc['month']
            rc.at['month'] = temp
        if errortype == 'rsd':
            rc.at['day'] = '01'
            rc.at['month'] = '01'
        if errortype == 'chy':
            '''
            Original line of code provided by the paper’s authors
            if rc.at['year'] != 'NaT' and rc['year'] != '':
            '''
            if rc.at['year'] is not np.nan and rc['year'] != '':
                margin = random.choice(range(-5,5))
                rc.at['year'] = str( int(rc['year']) + margin)
        if errortype == 'chz':
            if len(str(rc['postcode']))== 4:
                selected_digit = random.choice(range(4))
                code = list(str(rc['postcode']))
                code[selected_digit] = str( random.choice(range(9)))
                rc.at['postcode'] = int(''.join(code))
        if errortype == 'mar':
            rc.at["surname"] = df.iloc[random.choice(range(len(df)))]['surname']
        if errortype == 'twi':
            rc.at["given_name"] = df.iloc[random.choice(range(len(df)))]['given_name']
        if errortype == 'add':
            rc.at['address_1'] = df.iloc[random.choice(range(len(df)))]['address_1']
            rc.at['address_2'] = df.iloc[random.choice(range(len(df)))]['address_2']
            rc.at['street_number'] = random.choice(range(500))
    return rc

In [14]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Preprocess
df = pd.read_csv(
    r"Data_to_produce_ePBRN_dataset/"+inputfile+".csv", 
    parse_dates=["date_of_birth"])

df["rec_id"] = range(len(df))
df['rec_id'] = df['rec_id'].astype(str)
df['day'] = df['date_of_birth'].dt.strftime('%d')
df['month'] = df['date_of_birth'].dt.strftime('%m')
df['year'] = df['date_of_birth'].dt.strftime('%Y')
df['postcode'] =   df['postcode'].fillna('0000')
df['postcode'] = df['postcode'].astype(int)
df['street_number'] =   df['street_number'].fillna('0')
df['street_number'] = df['street_number'].astype(int)
df = df.drop(["age", "phone_number", "soc_sec_id", "blocking_number", "date_of_birth"], axis=1)
for col in ["surname", "given_name", "address_1", "address_2", "day", "month"]:
    df[col] = df[col].fillna('')
    df[col] = df[col].astype(str)
df["match_id"] = range(len(df))
all_fields = df.columns.values.tolist()
all_fields.remove('rec_id')

print("Original dataset length:",len(df))
df.head()

Original dataset length: 9250
CPU times: user 74.9 ms, sys: 2.7 ms, total: 77.6 ms
Wall time: 78.9 ms


rec_id given_name        surname  street_number         address_1  \
0      0      riley         cowley              2   ballarat street   
1      1   maddison          hiley              5  limestone avenue   
2      2     thomas        roberts             49   fortescue place   
3      3     nasyah  van der ploeg            395    kenyon circuit   
4      4       zara          denne             19                     

          address_2     suburb  postcode state day month  year  match_id  
0                       laguna      4218   vic             NaN         0  
1        lochenfels     cobram      6415   nsw  14    04  1921         1  
2  dp 12750 talunga  leongatha      2911   qld  16    01  1907         2  
3                     oakleigh      2515   NaN             NaN         3  
4         bestblock  kingsford      5290    sa  11    11  1911         4

In [15]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Generate random indices for linkages
leng = len(df)
print("Process", inputfile, ", total records:", leng, "...")
no_double_linked = int(leng*count_shared[0]/100)
no_triple_linked = int(leng*count_shared[1]/100)
no_quad_linked = int(leng*count_shared[2]/100)
list_double_linked = random.sample(range(leng),k=no_double_linked)
remain = [item for item in range(leng) if item not in list_double_linked]
list_triple_linked = random.sample(remain,k=no_triple_linked)
remain = [item for item in remain if item not in list_triple_linked]
list_quad_linked = random.sample(remain,k=no_quad_linked)
print("Double links:", no_double_linked,". Triple links:",no_triple_linked,". Quad links:",no_quad_linked)
print("Total records after generated:", leng + no_double_linked + no_triple_linked*2 + no_quad_linked*3)
print("Matched pairs:", no_double_linked + no_triple_linked*3 + no_quad_linked*6)

Process ePBRN_D_original , total records: 9250 ...
Double links: 2103 . Triple links: 189 . Quad links: 4
Total records after generated: 11743
Matched pairs: 2694
CPU times: user 126 ms, sys: 1.17 ms, total: 127 ms
Wall time: 126 ms


In [16]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
df1 = df
j = 0
for list_linked in [list_double_linked, list_triple_linked, list_quad_linked]:
    j = j + 1
    for i in list_linked:
        for k in range(j):
            record_to_process = df.iloc[i]
            processed_rc = process_record(record_to_process)
            processed_rc.at["rec_id"] = processed_rc["rec_id"] + "-dup-" + str(k)
            df1 = df1.append(processed_rc)

# Save to disk    
outputpath = r"Data_to_produce_ePBRN_dataset/"+ outputfile + ".csv"
df1.to_csv(outputpath, index=False)
print("Saved to", outputpath)

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = rc['given_name'][0:-1]
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pa

<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:94: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docume

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = df.iloc[random.choice(range(len(df)))]['given_name']
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:49: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = ''
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = rc["surname"][0]
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is 

<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docume

...

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = rc['surname']
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = temp
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = rc['surname'][0:-1]
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:46: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = rc["surname"][0]
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs

Saved to Data_to_produce_ePBRN_dataset/ePBRN_D_dup.csv
CPU times: user 38.3 s, sys: 3.31 s, total: 41.6 s
Wall time: 41.7 s


/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:52: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = ''
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:86: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['year'] = str( int(rc['year']) + margin)
<timed exec>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:15: FutureWarning: The frame.append me

## 2.2 Producing ePBRN_F_dup.csv

In [17]:
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
inputfile = 'ePBRN_F_original' 
outputfile = 'ePBRN_F_dup'

In [18]:
'''
This code was slightly modified from the original source code provided by the paper’s authors

Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Input the percentage of  [2, 3, 4] shared records in one linkage:
count_shared = [1.68+21.0659, 1.9986 + 0.0471, 0.05]

# Assigning the weights for each type of error:

abr = 1 # abbreviation on surname: Michael -> M
jwd1 = 1 # join with dash: John Peter -> John-Peter, join surname and given name into surname
jwd2 = 1 # join with dash: John Peter -> John-Peter, join surname and given name into given name
jwb1 = 1 # join with blank: 
jwb2 = 1 # join with blank: 
drf = 1 # drop all tokens in any field
dlc1 = 1 # drop last character in surname: Peter -> Pete
dlc2 = 1 # drop last character in given name
swn = 1 # swap surname and given name: John Peter -> Peter John
#swc1 = 1 # swap character in surname: Peter -> Petre
#swc2 = 1 # swap character in given name: Peter -> Petre
swd = 1 # swap day and month fields: 12/04 -> 04/12
rsd = 1 # reset day and month: 12/04/1991 -> 01/01/1991
chy = 1 # change year of birth by a margin of (+/-)5 
#drz1 = 1 # drop leading zeros from day of birth: 02/04 -> 2/04
#drz2 = 1 # drop leading zeros from month of birth: 02/04 -> 02/4
chz = 1 # change any number of digit from zip code
mar = 1 # change the whole token of surname: Mary Ward -> Mary Winston
twi = 1 # duplicate all fields except given name: Micheal Williams -> Leo Williams
add = 1 # change the whole 3 fields of address by randomly replacing each field by any other row

all_error_types = ['abr','jwd1','jwd2','jwb1','jwb2' ,'drf','dlc1','dlc2','swn',
                   'rsd','chy','chz','mar','twi','add']
all_error_weights = [abr, jwd1, jwd2, jwb1, jwb2, drf, dlc1, dlc2, swn, rsd, chy, chz, mar, twi, add]
all_error_weights = all_error_weights/sum(np.asarray(all_error_weights))

def process_record(rc):
    no_error = np.random.poisson(1, 1)
    errortypes = choice(all_error_types, no_error, p=all_error_weights)
    for errortype in errortypes:
        if errortype == 'abr':
            if len(rc["surname"])>0:
                #rc["surname"] = rc["surname"][0]
                rc.at["surname"] = rc["surname"][0]
        if errortype == 'jwd1':
            rc.at["surname"] = rc["surname"]+'-' +rc["given_name"]
            rc.at["given_name"] = ''
        if errortype == 'jwd2':
            rc.at["given_name"] = rc["surname"]+'-' +rc["given_name"]
            rc.at["surname"] = ''
        if errortype == 'jwb1':
            rc.at["surname"] = rc["surname"]+' ' +rc["given_name"]
            rc.at["given_name"] = ''
        if errortype == 'jwb2':
            rc.at["given_name"] = rc["surname"]+' ' +rc["given_name"]
            rc.at["surname"] = ''
        if errortype == 'drf':    
            selected_field = random.choice(all_fields)
            rc.at[selected_field] = ''
        if errortype == 'dlc1':
            if len(rc["surname"])>0:
                rc.at["surname"] = rc['surname'][0:-1]
        if errortype == 'dlc2':
            if len(rc["given_name"])>0:
                rc.at["given_name"] = rc['given_name'][0:-1]
        if errortype == 'swn':
            temp = rc['given_name']
            rc.at["given_name"] = rc['surname']
            rc.at["surname"] = temp
        if errortype == 'swd': 
            temp = rc['day']
            rc.at['day'] = rc['month']
            rc.at['month'] = temp
        if errortype == 'rsd':
            rc.at['day'] = '01'
            rc.at['month'] = '01'
        if errortype == 'chy':
            '''
            Original line of code provided by the paper’s authors
            if rc.at['year'] != 'NaT' and rc['year'] != '':
            '''
            if rc.at['year'] is not np.nan and rc['year'] != '':
                margin = random.choice(range(-5,5))
                rc.at['year'] = str( int(rc['year']) + margin)
        if errortype == 'chz':
            if len(str(rc['postcode']))== 4:
                selected_digit = random.choice(range(4))
                code = list(str(rc['postcode']))
                code[selected_digit] = str( random.choice(range(9)))
                rc.at['postcode'] = int(''.join(code))
        if errortype == 'mar':
            rc.at["surname"] = df.iloc[random.choice(range(len(df)))]['surname']
        if errortype == 'twi':
            rc.at["given_name"] = df.iloc[random.choice(range(len(df)))]['given_name']
        if errortype == 'add':
            rc.at['address_1'] = df.iloc[random.choice(range(len(df)))]['address_1']
            rc.at['address_2'] = df.iloc[random.choice(range(len(df)))]['address_2']
            rc.at['street_number'] = random.choice(range(500))
    return rc

In [19]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Preprocess
df = pd.read_csv(
    r"Data_to_produce_ePBRN_dataset/"+inputfile+".csv", 
    parse_dates=["date_of_birth"])

df["rec_id"] = range(len(df))
df['rec_id'] = df['rec_id'].astype(str)
df['day'] = df['date_of_birth'].dt.strftime('%d')
df['month'] = df['date_of_birth'].dt.strftime('%m')
df['year'] = df['date_of_birth'].dt.strftime('%Y')
df['postcode'] =   df['postcode'].fillna('0000')
df['postcode'] = df['postcode'].astype(int)
df['street_number'] =   df['street_number'].fillna('0')
df['street_number'] = df['street_number'].astype(int)
df = df.drop(["age", "phone_number", "soc_sec_id", "blocking_number", "date_of_birth"], axis=1)
for col in ["surname", "given_name", "address_1", "address_2", "day", "month"]:
    df[col] = df[col].fillna('')
    df[col] = df[col].astype(str)
df["match_id"] = range(len(df))
all_fields = df.columns.values.tolist()
all_fields.remove('rec_id')

print("Original dataset length:",len(df))
df.head()

Original dataset length: 11100
CPU times: user 90.8 ms, sys: 2.83 ms, total: 93.7 ms
Wall time: 93.7 ms


rec_id given_name   surname  street_number         address_1 address_2  \
0      0      jenna    kilpin            179    mcfarlan place             
1      1     bianca  randazzo             37  lindrum crescent  sunshine   
2      2      james   borlase             75                     rocklea   
3      3   nicholas    beeton             20         mugga way             
4      4      megan   footner              4      jewell close             

          suburb  postcode state day month  year  match_id  
0       hillarys      2768   vic  26    02  1950         0  
1        forster      2281    wa  07    04  1988         1  
2         casula      2460   qld  03    09  1913         2  
3       hawthorn      2480   vic  22    06  1999         3  
4  taylors lakes      3129   tas  22    09  1912         4

In [20]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Generate random indices for linkages
leng = len(df)
print("Process", inputfile, ", total records:", leng, "...")
no_double_linked = int(leng*count_shared[0]/100)
no_triple_linked = int(leng*count_shared[1]/100)
no_quad_linked = int(leng*count_shared[2]/100)
list_double_linked = random.sample(range(leng),k=no_double_linked)
remain = [item for item in range(leng) if item not in list_double_linked]
list_triple_linked = random.sample(remain,k=no_triple_linked)
remain = [item for item in remain if item not in list_triple_linked]
list_quad_linked = random.sample(remain,k=no_quad_linked)
print("Double links:", no_double_linked,". Triple links:",no_triple_linked,". Quad links:",no_quad_linked)
print("Total records after generated:", leng + no_double_linked + no_triple_linked*2 + no_quad_linked*3)
print("Matched pairs:", no_double_linked + no_triple_linked*3 + no_quad_linked*6)

Process ePBRN_F_original , total records: 11100 ...
Double links: 2524 . Triple links: 227 . Quad links: 5
Total records after generated: 14093
Matched pairs: 3235
CPU times: user 182 ms, sys: 1.31 ms, total: 183 ms
Wall time: 183 ms


In [21]:
%%time
'''
Source: 
K. Vo, J. Jonnagaddala and S.-T. Liaw, "Medical-Record-Linkage-Ensemble," 16 February 2019. [Online]. 
Available: https://github.com/ePBRN/Medical-Record-Linkage-Ensemble/.
'''
# Main steps
df1 = df
j = 0
for list_linked in [list_double_linked, list_triple_linked, list_quad_linked]:
    j = j + 1
    for i in list_linked:
        for k in range(j):
            record_to_process = df.iloc[i]
            # print(record_to_process)
            processed_rc = process_record(record_to_process)
            processed_rc.at["rec_id"] = processed_rc["rec_id"] + "-dup-" + str(k)
            df1 = df1.append(processed_rc)

# Save to disk    
outputpath = r"Data_to_produce_ePBRN_dataset/"+ outputfile + ".csv"
df1.to_csv(outputpath, index=False)
print("Saved to", outputpath)

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:96: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = df.iloc[random.choice(range(len(df)))]['given_name']
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing

<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at[selected_field] = ''
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/u

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:70: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["given_name"] = rc['surname']
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = temp
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['month'] = '01'
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:48: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at["surname"] = rc["surname"]+'-' +rc["given_name"]
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:49: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returnin

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['month'] = '01'
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:64: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_g

...

<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/i

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:98: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['address_1'] = df.iloc[random.choice(range(len(df)))]['address_1']
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:99: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['address_2'] = df.iloc[random.choice(range(len(df)))]['address_2']
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:100: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://

/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:77: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['day'] = '01'
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:78: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rc.at['month'] = '01'
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will

Saved to Data_to_produce_ePBRN_dataset/ePBRN_F_dup.csv
CPU times: user 46.9 s, sys: 4.18 s, total: 51.1 s
Wall time: 51.2 s


<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
<timed exec>:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
<timed exec>:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
/var/folders/7t/8q7jrbms6zng7kl7df_mf6_c0000gn/T/ipykernel_31608/3771546087.py:67: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docume